In [12]:
%config IPCompleter.greedy=True
import re
import json
from collections import defaultdict
from tqdm import tqdm_notebook as tqdm
from elasticsearch import Elasticsearch
from elasticsearch.helpers import parallel_bulk
from pymystem3 import Mystem
from sklearn.feature_extraction.text import CountVectorizer
import requests
from time import time
import glob
from datetime import datetime
import os


es = Elasticsearch([{'host': 'localhost', 'port': 9200, 'timeout': 360, 'maxsize': 25}])

In [13]:
ids = set()
ranks = {}
with open("page_ranks.csv", 'r') as f:
    lines = f.readlines()
    for line in lines:
        id, val = line.split()
        val = float(val)
        ranks[id] = val
        ids.add(id)

In [14]:
settings = {
    'mappings': {
        'properties': {
            'content': {
                'type': 'text'
            },
            'pagerank': {
                'type': 'rank_feature'
            },
        }
    },
    'settings': {
        'analysis': {
            'analyzer': {
                'russian_complex': {
                    'tokenizer': 'word_longer_2',
                    'filter': [
                        'lowercase',
                        'russian_snow'
                    ]
                }
            },
            'tokenizer': {
                'word_longer_2': {
                    'type': 'pattern',
                    'pattern': '[a-zA-Z_0-9\u0400-\u04FF]{2,}',
                    'group': 0
                }
            },
            'filter': {
                'russian_snow': {
                    'type': 'snowball',
                    'language': 'russian'
                }
            }
        }
    }
}

In [15]:
def recreate_index():
    es.indices.delete(index='myandex')
    es.indices.create(index='myandex', body=settings)
recreate_index()

In [16]:
def create_es_action(index, doc_id, document):
    return {
        '_index': index,
        '_id': doc_id,
        '_source': {'content': document, 'pagerank': 0.001 if (doc_id not in ranks) else ranks[doc_id]},
    }

def es_actions_generator():
    files = [f"text/document{id}.txt" for id in ids]
    for filename in glob.glob("text/document*.txt"):
        with open(filename, 'r') as inf:
            doc = json.dumps({'content': inf.read()})
        doc_id = (os.path.splitext(os.path.basename(inf.name))[0])[8:]
        yield create_es_action('myandex', doc_id, doc)

In [17]:
now = datetime.now()
print(now)
for ok, result in parallel_bulk(es, es_actions_generator(), queue_size=400000, thread_count=16, chunk_size=500):
    if not ok:
        print(result)
now = datetime.now()
print(now)

2019-09-28 04:18:35.712219
2019-09-28 05:42:54.483540


In [18]:
es.indices.stats()

{'_shards': {'total': 2, 'successful': 1, 'failed': 0},
 '_all': {'primaries': {'docs': {'count': 197824, 'deleted': 0},
   'store': {'size_in_bytes': 3032588165},
   'indexing': {'index_total': 200000,
    'index_time_in_millis': 518399,
    'index_current': 0,
    'index_failed': 0,
    'delete_total': 0,
    'delete_time_in_millis': 0,
    'delete_current': 0,
    'noop_update_total': 0,
    'is_throttled': False,
    'throttle_time_in_millis': 0},
   'get': {'total': 0,
    'time_in_millis': 0,
    'exists_total': 0,
    'exists_time_in_millis': 0,
    'missing_total': 0,
    'missing_time_in_millis': 0,
    'current': 0},
   'search': {'open_contexts': 0,
    'query_total': 0,
    'query_time_in_millis': 0,
    'query_current': 0,
    'fetch_total': 0,
    'fetch_time_in_millis': 0,
    'fetch_current': 0,
    'scroll_total': 0,
    'scroll_time_in_millis': 0,
    'scroll_current': 0,
    'suggest_total': 0,
    'suggest_time_in_millis': 0,
    'suggest_current': 0},
   'merges': 

In [19]:
def search(query, *args):
    return es.search(index='myandex', body=query, size=100)
    # note that size set to 20 just because default value is 10 and we know that we have 12 docs and 10 < 12 < 20
                        
def pretty_print_result(search_result, fields=[]):
    # fields is a list of fields names which we want to be printed
    res = search_result['hits']
    print(f'Total documents: {res["total"]["value"]}')
    data = {}
    for hit in res['hits']:
        data[hit['_id']] = hit['_source']['pagerank']
    return data
                  
def get_doc_by_id(doc_id):
    return es.get(index='myandex', id=doc_id)['_source']

In [20]:
query = {
    'query': {
        'match_all': {}
    }
}

search(query, ' ')

{'took': 4024,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 10000, 'relation': 'gte'},
  'max_score': 1.0,
  'hits': [{'_index': 'myandex',
    '_type': '_doc',
    '_id': '782418',
    '_score': 1.0,
    '_source': {'content': '{"content": "MP3 FLASH \\u041f\\u041b\\u0415\\u0415\\u0420\\u042b :: KINGSTON :: FLASH\\u00a0\\u00a0\\u0413\\u043b\\u0430\\u0432\\u043d\\u0430\\u044f \\u00bb MP3 FLASH \\u041f\\u041b\\u0415\\u0415\\u0420\\u042b \\u00bb KINGSTON\\u00a0\\u00a0\\u0412\\u0445\\u043e\\u0434 \\u00a0|\\u00a0 \\u041a\\u043e\\u0440\\u0437\\u0438\\u043d\\u0430 \\u00a0|\\u00a0 \\u041e\\u0444\\u043e\\u0440\\u043c\\u0438\\u0442\\u044c \\u0437\\u0430\\u043a\\u0430\\u0437 \\u00a0\\u00a0\\u00a0\\u0420\\u0430\\u0437\\u0434\\u0435\\u043b\\u044bMP3 FLASH \\u041f\\u041b\\u0415\\u0415\\u0420\\u042b\\u00a0(148)SPEED\\u00a0(0)MEIZU\\u00a0(4)DELTA\\u00a0(18)LUXPRO\\u00a0(12)SONY\\u00a0(6)IRIVER\\u00a0(13)JAGGA\\u00a0(26)KINGSTO

In [27]:
def create_query(text):
    query = {
        'query': {
            'bool': {
                'should': [
                    {
                        'match': {
                            'content': text
                        }
                    },
                    {
                        'rank_feature': {
                            'field': 'pagerank',
                            'boost': 0.3,
                            'log': {
                                'scaling_factor': 10
                            }
                        }
                    }
                ]
            }
        }
    }
    return query

In [28]:
from bs4 import BeautifulSoup

file = f"web2008_adhoc.xml"
f = open(file, "rb")
contents = f.read()
soup = BeautifulSoup(contents, 'xml')
        
table = {}
for task in soup.find_all('task'):
    text = task.querytext.text
    data = search(create_query(text), ' ')
    table[task['id']] = pretty_print_result(data)

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

...

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total documents: 10000
Total docum

In [29]:
file = f"relevant_table_2009.xml"

def get_relevance():
    relevance = {}
    with open(file,'r', encoding="cp1251") as src:
        raw_xml = src.read()
        soup = BeautifulSoup(raw_xml)
        for task in soup.find_all('task'):
            documents = task.find_all('document') 
            vital = set()
            for doc in documents:
                if doc['relevance'] == 'vital':
                    vital.add(doc['id'])
            if vital:
                relevance[task['id']] = vital
    return relevance
relevance = get_relevance()

In [30]:
file = f"web2008_adhoc.xml"

def get_query_ids():
    f = open(file, "rb")
    contents = f.read()
    soup = BeautifulSoup(contents, 'xml')
    queries = []
    for task in soup.find_all('task'):
        if task['id'] in table:
            queries.append(task['id'])
    return queries

queries = get_query_ids()

In [35]:
K = 20

def get_relevant_for_k(res, relevant, k):
    return sum([1 if doc in relevant else 0 for doc in res[:k]])        

def analyze_results():
    Q = 0
    qpK, qrK, qR_average, qmapK = 0, 0, 0, 0
    qR = []
    for task_id in queries:
        results = [k for k in table[task_id]][:K]
        if task_id not in relevance:
            continue
        Q += 1
        cur_relevant = len(relevance[task_id])
        qpK += get_relevant_for_k(results, relevance[task_id], K) / K 
        qrK += get_relevant_for_k(results, relevance[task_id], K) / cur_relevant
        qR.append(get_relevant_for_k(results, relevance[task_id], cur_relevant) / cur_relevant)
        qR_average += qR[-1]
        mapK = 0
        for k in range(1, K + 1):
            mapK += get_relevant_for_k(results, relevance[task_id], k) / k
        mapK /= K
        qmapK += mapK
    print(f"p@20 {qpK / Q}")
    print(f"r@20 {qrK / Q}")
    print(f"R-precision {qR_average / Q}")
    print(f"Average MAP@20 {qmapK / Q}")

In [36]:
analyze_results()

p@20 0.4101010101010102
r@20 0.24899739923384745
R-precision 0.206771923184842
Average MAP@20 0.44141791152404247
